In [2]:
import geopandas as gpd

# Read the files and reproject to EPSG:3067
stops = gpd.read_file("data/Helsinki/pt_stops_helsinki.gpkg").to_crs(epsg=3067)
building_points = gpd.read_file("data/Helsinki/building_points_helsinki.zip").to_crs(
    epsg=3067
)

building_points.head(2)

name                        geometry
0         None    POINT (381166.6 6676424.438)
1  Uimastadion  POINT (385236.565 6674238.472)

In [3]:
stops.shape

(8377, 5)

In [4]:
stops.head()

stop_name   stop_lat   stop_lon  stop_id                        geometry
0  Ritarihuone  60.169460  24.956670  1010102  POINT (386623.301 6672037.884)
1   Kirkkokatu  60.171270  24.956570  1010103  POINT (386623.991 6672239.572)
2   Kirkkokatu  60.170293  24.956721  1010104      POINT (386629 6672130.538)
3    Vironkatu  60.172580  24.956554  1010105  POINT (386627.617 6672385.448)
4    Vironkatu  60.172990  24.956380  1010106  POINT (386619.379 6672431.394)

In [5]:
building_coords = building_points.get_coordinates().to_numpy()
stop_coords = stops.geometry.get_coordinates().to_numpy()

stop_coords

array([[ 386623.30055697, 6672037.88387715],
       [ 386623.99053928, 6672239.57164472],
       [ 386629.00011373, 6672130.5382358 ],
       ...,
       [ 393706.51571504, 6707260.21305267],
       [ 391372.74617002, 6697807.78260742],
       [ 388733.41604041, 6714694.15542812]])

In [6]:
from scipy.spatial import KDTree

stop_kdt = KDTree(stop_coords)
stop_kdt

In [7]:
# Find the three nearest neighbors from stop KD-Tree for each building
k_nearest_dist, k_nearest_ix = stop_kdt.query(building_coords, k=3)

len(k_nearest_dist)

158731

In [8]:
# Make a copy
k_nearest = building_points.copy()

# Add indices of nearest stops
k_nearest["1st_nearest_idx"] = k_nearest_ix.T[0]
k_nearest["2nd_nearest_idx"] = k_nearest_ix.T[1]
k_nearest["3rd_nearest_idx"] = k_nearest_ix.T[2]

# Add distances
k_nearest["1st_nearest_dist"] = k_nearest_dist.T[0]
k_nearest["2nd_nearest_dist"] = k_nearest_dist.T[1]
k_nearest["3rd_nearest_dist"] = k_nearest_dist.T[2]

In [10]:
k_nearest.head()

name                        geometry  1st_nearest_idx  \
0            None    POINT (381166.6 6676424.438)             1131   
1     Uimastadion  POINT (385236.565 6674238.472)              467   
2            None  POINT (386317.478 6672100.648)               61   
3  Hartwall Arena   POINT (385225.109 6676120.56)              532   
4           Talli  POINT (385079.733 6676989.745)              496   

   2nd_nearest_idx  3rd_nearest_idx  1st_nearest_dist  2nd_nearest_dist  \
0             1135             1125         92.679893        461.438204   
1              465              475        400.243370        409.497073   
2               64               13        109.819633        130.597498   
3              533              506        104.632434        137.706391   
4              497              498        472.248282        519.685534   

   3rd_nearest_dist  
0        466.169150  
1        410.061370  
2        133.642481  
3        377.331985  
4        551.358778

In [11]:
# Store the stop index for making the table join
stops["stop_index"] = stops.index

In [12]:
# Merge the geometries of the nearest stops to the GeoDataFrame
k_nearest_1 = k_nearest.merge(
    stops[["stop_index", "geometry"]],
    left_on="1st_nearest_idx",
    right_on="stop_index",
    suffixes=("", "_knearest"),
)
k_nearest_1.head(2)

name                        geometry  1st_nearest_idx  \
0         None    POINT (381166.6 6676424.438)             1131   
1  Uimastadion  POINT (385236.565 6674238.472)              467   

   2nd_nearest_idx  3rd_nearest_idx  1st_nearest_dist  2nd_nearest_dist  \
0             1135             1125         92.679893        461.438204   
1              465              475        400.243370        409.497073   

   3rd_nearest_dist  stop_index               geometry_knearest  
0         466.16915        1131   POINT (381256.66 6676446.317)  
1         410.06137         467  POINT (384973.331 6674539.973)

In [13]:
# Merge the geometries of the 2nd nearest stops to the GeoDataFrame
k_nearest_2 = k_nearest.merge(
    stops[["stop_index", "geometry"]],
    left_on="2nd_nearest_idx",
    right_on="stop_index",
    suffixes=("", "_knearest"),
)
k_nearest_2.head(2)

name                        geometry  1st_nearest_idx  \
0         None    POINT (381166.6 6676424.438)             1131   
1  Uimastadion  POINT (385236.565 6674238.472)              467   

   2nd_nearest_idx  3rd_nearest_idx  1st_nearest_dist  2nd_nearest_dist  \
0             1135             1125         92.679893        461.438204   
1              465              475        400.243370        409.497073   

   3rd_nearest_dist  stop_index               geometry_knearest  
0         466.16915        1135  POINT (381625.316 6676474.488)  
1         410.06137         465  POINT (385270.775 6674646.538)

In [14]:
# Merge the geometries of the 3rd nearest stops to the GeoDataFrame
k_nearest_3 = k_nearest.merge(
    stops[["stop_index", "geometry"]],
    left_on="3rd_nearest_idx",
    right_on="stop_index",
    suffixes=("", "_knearest"),
)
k_nearest_3.head(2)

name                        geometry  1st_nearest_idx  \
0         None    POINT (381166.6 6676424.438)             1131   
1  Uimastadion  POINT (385236.565 6674238.472)              467   

   2nd_nearest_idx  3rd_nearest_idx  1st_nearest_dist  2nd_nearest_dist  \
0             1135             1125         92.679893        461.438204   
1              465              475        400.243370        409.497073   

   3rd_nearest_dist  stop_index              geometry_knearest  
0         466.16915        1125  POINT (381632.74 6676429.668)  
1         410.06137         475  POINT (385122.17 6674632.254)

In [15]:
from shapely import LineString

# Generate LineStrings connecting the building point and K-nearest neighbor
k_nearest_1["geometry"] = k_nearest_1.apply(
    lambda row: LineString([row["geometry"], row["geometry_knearest"]]), axis=1
)
k_nearest_2["geometry"] = k_nearest_2.apply(
    lambda row: LineString([row["geometry"], row["geometry_knearest"]]), axis=1
)
k_nearest_3["geometry"] = k_nearest_3.apply(
    lambda row: LineString([row["geometry"], row["geometry_knearest"]]), axis=1
)

k_nearest_1.head(2)

name                                           geometry  \
0         None  LINESTRING (381166.6 6676424.438, 381256.66 66...   
1  Uimastadion  LINESTRING (385236.565 6674238.472, 384973.331...   

   1st_nearest_idx  2nd_nearest_idx  3rd_nearest_idx  1st_nearest_dist  \
0             1131             1135             1125         92.679893   
1              467              465              475        400.243370   

   2nd_nearest_dist  3rd_nearest_dist  stop_index  \
0        461.438204         466.16915        1131   
1        409.497073         410.06137         467   

                geometry_knearest  
0   POINT (381256.66 6676446.317)  
1  POINT (384973.331 6674539.973)

In [17]:
# Visualize 3 nearest stops to
selected_name = "Hartwall Arena"

m = k_nearest_1.loc[k_nearest_1["name"] == selected_name].explore(
    color="red", tiles="CartoDB Positron", max_zoom=16
)
m = k_nearest_2.loc[k_nearest_2["name"] == selected_name].explore(m=m, color="orange")
m = k_nearest_3.loc[k_nearest_3["name"] == selected_name].explore(m=m, color="blue")
m = stops.explore(m=m, color="green")
m

In [18]:
from scipy.spatial import KDTree

# Build KDTree indices
stop_kdt = KDTree(stop_coords)
building_kdt = KDTree(building_coords)

# Find the three nearest neighbors from stop KD-Tree for each building
k_nearest_ix = stop_kdt.query_ball_tree(building_kdt, r=200)

In [19]:
k_nearest_ix[0]

[1129,
 1130,
 1155,
 2054,
 2055,
 2056,
 2057,
 2058,
 2059,
 9910,
 9955,
 9956,
 9957,
 10993,
 25983,
 25984,
 25985,
 25986,
 26029,
 26030,
 26031,
 26032,
 26033,
 28253,
 35395,
 35397,
 35400,
 35401,
 35418,
 35420,
 35421,
 35460,
 48124,
 48284,
 48285,
 49383,
 58133,
 58181,
 58182,
 58201,
 58203,
 58204,
 58208,
 58209,
 58210,
 58211,
 58212,
 58318,
 58320,
 58378]

In [20]:
stops["building_ids_within_range"] = k_nearest_ix
stops.head()

stop_name   stop_lat   stop_lon  stop_id                        geometry  \
0  Ritarihuone  60.169460  24.956670  1010102  POINT (386623.301 6672037.884)   
1   Kirkkokatu  60.171270  24.956570  1010103  POINT (386623.991 6672239.572)   
2   Kirkkokatu  60.170293  24.956721  1010104      POINT (386629 6672130.538)   
3    Vironkatu  60.172580  24.956554  1010105  POINT (386627.617 6672385.448)   
4    Vironkatu  60.172990  24.956380  1010106  POINT (386619.379 6672431.394)   

   stop_index                          building_ids_within_range  
0           0  [1129, 1130, 1155, 2054, 2055, 2056, 2057, 205...  
1           1  [1130, 2054, 2055, 2057, 2058, 2059, 2066, 206...  
2           2  [1129, 1130, 2054, 2055, 2056, 2057, 2058, 205...  
3           3  [2060, 2062, 2063, 2064, 2065, 2066, 2067, 206...  
4           4  [1136, 2060, 2061, 2062, 2063, 2064, 2065, 206...

In [21]:
stops["building_cnt"] = stops["building_ids_within_range"].apply(
    lambda id_list: len(id_list)
)
stops.head()

stop_name   stop_lat   stop_lon  stop_id                        geometry  \
0  Ritarihuone  60.169460  24.956670  1010102  POINT (386623.301 6672037.884)   
1   Kirkkokatu  60.171270  24.956570  1010103  POINT (386623.991 6672239.572)   
2   Kirkkokatu  60.170293  24.956721  1010104      POINT (386629 6672130.538)   
3    Vironkatu  60.172580  24.956554  1010105  POINT (386627.617 6672385.448)   
4    Vironkatu  60.172990  24.956380  1010106  POINT (386619.379 6672431.394)   

   stop_index                          building_ids_within_range  building_cnt  
0           0  [1129, 1130, 1155, 2054, 2055, 2056, 2057, 205...            50  
1           1  [1130, 2054, 2055, 2057, 2058, 2059, 2066, 206...            69  
2           2  [1129, 1130, 2054, 2055, 2056, 2057, 2058, 205...            56  
3           3  [2060, 2062, 2063, 2064, 2065, 2066, 2067, 206...            74  
4           4  [1136, 2060, 2061, 2062, 2063, 2064, 2065, 206...            78

In [22]:
filtered = stops["building_cnt"] == stops["building_cnt"].max()
building_ids = stops.loc[filtered].building_ids_within_range.values[0]

m = stops.loc[filtered].explore(
    tiles="CartoDB Positron", color="red", marker_kwds={"radius": 5}, max_zoom=16
)
building_points.loc[building_ids].explore(m=m)